In [1]:
import pickle
import csv
import numpy as np
import pandas as pd
from scipy import stats
import matplotlib.pyplot as plt
import seaborn as sns

In [2]:
results_folder = 'Q:\\Personal\\Irina\\projects\\isttc\\results\\monkey\\'

### Load data

In [3]:
csv_data_file_pfdl = results_folder + 'data_pfdl_fixon_1500ms_fixation.csv'
with open(csv_data_file_pfdl, newline='') as f:
    reader = csv.reader(f)
    sua_list_pfdl = list(reader)
    
n_spike_trains_pfdl = len(sua_list_pfdl)
print('N spike_trains in PFdl fixON {}'.format(n_spike_trains_pfdl))

N spike_trains in PFdl fixON 33018


In [4]:
csv_data_file_pfp = results_folder + 'data_pfp_fixon_1500ms_fixation.csv'
with open(csv_data_file_pfp, newline='') as f:
    reader = csv.reader(f)
    sua_list_pfp = list(reader)

n_spike_trains_pfp = len(sua_list_pfp)
print('N spike_trains in PFp fixON {}'.format(n_spike_trains_pfp))

N spike_trains in PFp fixON 27717


In [5]:
pfdl_summary_df = pd.read_pickle(results_folder + 'pfdl_n_trials_per_unit_merged_fixon.pkl')
pfp_summary_df = pd.read_pickle(results_folder + 'pfp_n_trials_per_unit_merged_fixon.pkl')

In [ ]:
pfdl_summary_df

### Get the FR

In [ ]:
unit_id_pfdl_l = []
spike_count_pfdl_l = []

for unit in sua_list_pfdl:
    unit_id_pfdl_l.append(unit[0])
    spike_count_pfdl_l.append(len(unit[3:]))

fr_pfdl_df = pd.DataFrame(np.vstack((unit_id_pfdl_l, spike_count_pfdl_l)).T, 
                                         columns=['unit_id', 'spike_count'])
fr_pfdl_df['unit_id'] = fr_pfdl_df['unit_id'].astype(int)
fr_pfdl_df['spike_count'] = fr_pfdl_df['spike_count'].astype(float)
fr_pfdl_df['fr_hz'] = fr_pfdl_df['spike_count'] / 1.5
fr_pfdl_df['fr_hz_log10'] = np.log10(fr_pfdl_df['fr_hz'])

fr_pfdl_df

In [ ]:
fr_pfdl_df_mean = fr_pfdl_df.groupby(by='unit_id', as_index=False)[['spike_count', 'fr_hz']].mean()
fr_pfdl_df_mean

In [ ]:
fr_pfdl_df_med = fr_pfdl_df.groupby(by='unit_id', as_index=False)[['spike_count', 'fr_hz']].median()
fr_pfdl_df_med

In [ ]:
fr_pfdl_df_std = fr_pfdl_df.groupby(by='unit_id', as_index=False)[['spike_count', 'fr_hz']].std()
fr_pfdl_df_std.rename(columns={'spike_count':'spike_count_std', 'fr_hz': 'fr_hz_std'}, inplace=True)
fr_pfdl_df_std

In [ ]:
fr_pfdl_df_avg = fr_pfdl_df_mean.merge(fr_pfdl_df_med, on='unit_id', how='left', suffixes=('_mean', '_med'))
fr_pfdl_df_avg = fr_pfdl_df_avg.merge(fr_pfdl_df_std, on='unit_id', how='left')
fr_pfdl_df_avg

In [ ]:
# plot without grouping per animal (across trials)
perc_trials_above1hz = np.round(len(fr_pfdl_df.query('fr_hz >= 1'))/len(fr_pfdl_df) * 100, 2)
mean_fr = np.round(np.nanmean(fr_pfdl_df['fr_hz'].values), 2)
med_fr = np.round(np.nanmedian(fr_pfdl_df['fr_hz'].values),2)

fig, axes = plt.subplots(1, 2, figsize=(8,3))

sns.violinplot(ax=axes[0], y='fr_hz_log10', data=fr_pfdl_df, cut=0, density_norm='width')
sns.violinplot(ax=axes[1], y='fr_hz', data=fr_pfdl_df, cut=0, density_norm='width')

axes[0].set_title('% trials with fr >= 1hz: {}'.format(perc_trials_above1hz))
axes[1].set_title('Mean fr {}, mead fr {}'.format(mean_fr, med_fr))

axes[0].axhline(y=np.log10(1), lw=1, color='red')
axes[1].axhline(y=1, lw=1, color='red')

sns.despine()

In [ ]:
# plot with grouping per animal

fig, axes = plt.subplots(1, 2, figsize=(8,3))

sns.violinplot(ax=axes[0], y='fr_hz_mean', data=fr_pfdl_df_avg, cut=0, density_norm='width')
sns.violinplot(ax=axes[1], y='fr_hz_med', data=fr_pfdl_df_avg, cut=0, density_norm='width')

# axes[0].set_title('% trials with fr >= 1hz: {}'.format(perc_trials_above1hz))
# axes[1].set_title('Mean fr {}, mead fr {}'.format(mean_fr, med_fr))

axes[0].axhline(y=1, lw=1, color='red')
axes[1].axhline(y=1, lw=1, color='red')

sns.despine()

In [ ]:
# plot

fig, axes = plt.subplots(1, 2, figsize=(8,3))

sns.scatterplot(ax=axes[0], x='fr_hz_mean', y='fr_hz_med', data=fr_pfdl_df_avg)
sns.scatterplot(ax=axes[1], x='fr_hz_mean', y='fr_hz_med', data=fr_pfdl_df_avg)

# axes[0].set_title('% trials with fr >= 1hz: {}'.format(perc_trials_above1hz))
# # axes[1].set_title('N trials per unit, PFp')

# axes[0].axhline(y=np.log10(1), lw=1, color='red')
# axes[1].axhline(y=1, lw=1, color='red')

axes[1].set_xlim([0,2])
axes[1].set_ylim([0,2])

sns.despine()

### Bin spikes (50ms bins)

In [6]:
def bin_spike_train(spike_train_int_l_, bin_length_ms_, fs_, verbose_=True):
    """
    Bin spike train.

    :param spike_train_int_l_: list, list of spike times (int), sampling frequency fs_
    :param bin_length_ms_: int, bin length in ms
    :param fs_: int, sampling frequency in Hz
    :param verbose_: bool, default False, diagnostic printout if True, silent otherwise
    :return: 1d array, binned spike train, each bin contains spike count
    """
    bin_length_fs = int(fs_ / 1000 * bin_length_ms_)
    #n_bin_edges = int(np.ceil(spike_train_int_l_[-1] / bin_length_fs))  # using ceil to include the last spike
    n_bin_edges =  int(1500/bin_length_fs)
    bins_ = np.linspace(0, bin_length_fs * n_bin_edges, n_bin_edges + 1).astype(int)
    binned_spike_train, _ = np.histogram(spike_train_int_l_, bins_)

    if verbose_:
        print('Binning spike train: bin_length_ms {}, bin_length_fs {}'.format(bin_length_ms_, bin_length_fs))
        print('n bins {}, spike bin count: number of spikes in bin - number of bins {}'.format(binned_spike_train.shape,
                                                                                               np.unique(
                                                                                                   binned_spike_train,
                                                                                                   return_counts=True)))

    return binned_spike_train

In [7]:
unit_id_pfdl_l = []
trial_id_pfdl_l = []
condition_id_pfdl_l = []
spike_binned_pfdl_l = []

for unit in sua_list_pfdl:
    unit_id_pfdl_l.append(unit[0])
    trial_id_pfdl_l.append(unit[1])
    condition_id_pfdl_l.append(unit[2])

    spike_train = unit[3:]
    spike_train = [int(x) for x in spike_train]
    binned_spike_train = bin_spike_train(spike_train, 50, 1000, verbose_=True)
    spike_binned_pfdl_l.append(binned_spike_train)

Binning spike train: bin_length_ms 50, bin_length_fs 50
n bins (30,), spike bin count: number of spikes in bin - number of bins (array([0, 1, 2, 3], dtype=int64), array([19,  7,  2,  2], dtype=int64))
Binning spike train: bin_length_ms 50, bin_length_fs 50
n bins (30,), spike bin count: number of spikes in bin - number of bins (array([0, 1, 2], dtype=int64), array([17, 11,  2], dtype=int64))
Binning spike train: bin_length_ms 50, bin_length_fs 50
n bins (30,), spike bin count: number of spikes in bin - number of bins (array([0, 1, 2], dtype=int64), array([12, 12,  6], dtype=int64))
Binning spike train: bin_length_ms 50, bin_length_fs 50
n bins (30,), spike bin count: number of spikes in bin - number of bins (array([0, 1, 2, 3, 4], dtype=int64), array([ 2, 11, 10,  6,  1], dtype=int64))
Binning spike train: bin_length_ms 50, bin_length_fs 50
n bins (30,), spike bin count: number of spikes in bin - number of bins (array([0, 1, 2], dtype=int64), array([22,  6,  2], dtype=int64))
Binning s

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



Binning spike train: bin_length_ms 50, bin_length_fs 50
n bins (30,), spike bin count: number of spikes in bin - number of bins (array([0, 1], dtype=int64), array([25,  5], dtype=int64))
Binning spike train: bin_length_ms 50, bin_length_fs 50
n bins (30,), spike bin count: number of spikes in bin - number of bins (array([0, 1], dtype=int64), array([24,  6], dtype=int64))
Binning spike train: bin_length_ms 50, bin_length_fs 50
n bins (30,), spike bin count: number of spikes in bin - number of bins (array([0, 1, 2], dtype=int64), array([20,  9,  1], dtype=int64))
Binning spike train: bin_length_ms 50, bin_length_fs 50
n bins (30,), spike bin count: number of spikes in bin - number of bins (array([0, 1], dtype=int64), array([25,  5], dtype=int64))
Binning spike train: bin_length_ms 50, bin_length_fs 50
n bins (30,), spike bin count: number of spikes in bin - number of bins (array([0, 1], dtype=int64), array([26,  4], dtype=int64))
Binning spike train: bin_length_ms 50, bin_length_fs 50
n 

In [ ]:
spike_binned_pfdl_l

In [ ]:
# make a df with binned spikes

binned_spike_pfdl_df = pd.DataFrame(spike_binned_pfdl_l, columns=['bin' + str(i) for i in range(30)])
binned_spike_pfdl_df.insert(0, 'unit_id', unit_id_pfdl_l)
binned_spike_pfdl_df

In [ ]:
binned_spike_pfdl_df_mean = binned_spike_pfdl_df.groupby('unit_id', as_index=False).mean()
binned_spike_pfdl_df_mean

In [ ]:
cols = ['bin' + str(i) for i in range(30)]

sns.heatmap(binned_spike_pfdl_df_mean[cols].values)

In [ ]:
np.count_nonzero(binned_spike_pfdl_df_mean[cols].values == 0)

In [ ]:
cols_1000 = ['bin' + str(i) for i in range(20)]
len(binned_spike_pfdl_df_mean[(binned_spike_pfdl_df_mean[cols_1000].values == 0).any(axis=1)].index.values.tolist())

In [ ]:
543-161

In [ ]:
fig, axes = plt.subplots(1,1, figsize=(10,6))

#t_axis = np.linspace

for i in range(len(binned_spike_pfdl_df_mean)):
    axes.plot(binned_spike_pfdl_df_mean[cols].values[i,:], lw=0.5, c='k', alpha=0.5)

sns.despine()

In [ ]:
fig, axes = plt.subplots(1,1, figsize=(10,6))

#t_axis = np.linspace

for i in range(1):
    axes.plot(binned_spikes_mean_z[i,:], lw=0.5, c='k', alpha=0.5)

sns.despine()

In [ ]:
binned_spikes_mean_z = stats.zscore(binned_spike_pfdl_df_mean[cols].values, axis=1)
binned_spikes_mean_z.shape

In [ ]:
sns.heatmap(binned_spikes_mean_z)

### Average over trials (heatmaps)

lines - individual and average

### Save binned data

In [8]:
def write_csv(output_filename, unit_id_l, trial_id_l, condition_id_l, spike_trains_l, verbose=True):
    with open(output_filename, 'a', newline='') as f:
        writer = csv.writer(f)
        for unit_row_n, spike_train in enumerate(spike_trains_l):
            if verbose:
                print('Writing unit {}'.format(unit_id_l[unit_row_n]))
                # print(spike_train)
            spikes_l = spike_train.tolist()
            row = [unit_id_l[unit_row_n]] + [trial_id_l[unit_row_n]] + [condition_id_l[unit_row_n]] + spikes_l
            writer.writerow(row)

In [ ]:
spike_binned_pfdl_l[0]

In [9]:
output_filename_pfdl = results_folder + 'data_pfdl_fixon_1500ms_fixation_binned_50ms.csv'
write_csv(output_filename_pfdl, unit_id_pfdl_l, trial_id_pfdl_l, condition_id_pfdl_l, spike_binned_pfdl_l, verbose=False)